In [1]:
!pip install lime
!pip install KDEpy
!pip install fairlearn
!pip install scikit-learn==1.1.3
!pip install eli5

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 275.7/275.7 kB 7.0 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for lime: filename=lime-0.2.0.1-py3-none-any.whl size=283834 sha256=bdd8fbada1c424e6b7067e4a466b53fc010c98cfec7e72e159ee381fdd50ad8c
  Stored in directory: /root/.cache/pip/wheels/fd/a2/af/9ac0a1a85a27f314a06b39e1f492bee1547d52549a4606ed89
Successfully built lime
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 652.9/652.9 kB 16.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 232.3/232.3 kB 11.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 30.5/30.5 MB 48.8 MB/s eta 0:00:00
  Attempting uninstall: scikit-learn
    Found existing installation: scikit-learn 1.5.2
    Uninstalling scikit-learn-1.5.2:
      Successfully uninstalled scikit-learn-1.5.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
bigfr

In [2]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import scipy as sp
from KDEpy import FFTKDE
import sklearn as sk
import seaborn as sns
import plotly.express as px
import fairlearn as fl
import eli5
import shap
import lime as lm


/usr/local/lib/python3.10/dist-packages/dask/dataframe/__init__.py:42: FutureWarning: 
Dask dataframe query planning is disabled because dask-expr is not installed.

You can install it with `pip install dask[dataframe]` or `conda install dask`.
This will raise in a future version.

  warnings.warn(msg, FutureWarning)


In [3]:
!pip install update scikit-learn

In [4]:
import sklearn as sk

In [5]:
import folium as fl

In [6]:
from folium.plugins import HeatMap

In [8]:
df = pd.read_csv("/content/Crimes_-_2019_20241207.csv")

In [9]:
df = df.dropna()

In [10]:
df_for_heatmap = df[["Latitude", "Longitude"]]

In [11]:
map_center = [df_for_heatmap["Latitude"].mean(), df_for_heatmap["Longitude"].mean()]
crimes_heatmap = fl.Map(location=map_center, zoom_start=15)
HeatMap(df_for_heatmap).add_to(crimes_heatmap)
crimes_heatmap

In [12]:
df['Date'] = pd.to_datetime(df['Date'])
df['hour'] = df['Date'].dt.hour
df['day_of_week'] = df['Date'].dt.dayofweek
df['month'] = df['Date'].dt.month
df['year'] = df['Date'].dt.year

In [13]:
df['hour_sin'] = np.sin(df['hour'] * (2 * np.pi / 24))
df['hour_cos'] = np.cos(df['hour'] * (2 * np.pi / 24))
df['day_of_week_sin'] = np.sin(df['day_of_week'] * (2 * np.pi / 7))
df['day_of_week_cos'] = np.cos(df['day_of_week'] * (2 * np.pi / 7))
df['mont_sin'] = np.sin(df['month'] * (2 * np.pi / 12))
df['month_cos'] = np.cos(df['month'] * (2 * np.pi / 12))

In [14]:
df = df.drop(['Case Number', 'IUCR', 'Updated On', 'Year', 'FBI Code', 'Description'], axis=1, errors='ignore')

In [15]:
crime_mapping = {
    "ROBBERY": "PROPERTY THEFT",
    "THEFT": "PROPERTY THEFT",
    "BURGLARY": "PROPERTY THEFT",
    "MOTOR VEHICLE THEFT": "PROPERTY THEFT",
    "CRIMINAL SEXUAL ASSAULT": "SEX CRIMES",
    "STALKING": "SEX CRIMES",
    "SEX OFFENSE": "SEX CRIMES",
    "CRIM SEXUAL ASSAULT": "SEX CRIMES",
    "PROSTITUTION": "SEX CRIMES",
    "BATTERY": "VIOLENT CRIMES",
    "WEAPONS VIOLATION": "VIOLENT CRIMES",
    "ASSAULT": "VIOLENT CRIMES",
    "CRIMINAL DAMAGE": "VIOLENT CRIMES",
    "ARSON": "VIOLENT CRIMES",
    "INTIMIDATION": "VIOLENT CRIMES",
    "NARCOTICS": "SUBSTANCE CRIMES",
    "LIQUOR LAW VIOLATION": "SUBSTANCE CRIMES",
    "OTHER NARCOTIC VIOLATION": "SUBSTANCE CRIMES",
    "PUBLIC INDECENCY": "CRIMES AGAINST PUBLIC",
    "OBSCENITY": "CRIMES AGAINST PUBLIC",
    "PUBLIC PEACE VIOLATION": "CRIMES AGAINST PUBLIC",
    "INTERFERENCE WITH PUBLIC OFFICER": "CRIMES AGAINST PUBLIC",
    "DECEPTIVE PRACTICE": "CRIMES AGAINST PUBLIC",
    "HUMAN TRAFFICKING": "ABDUCTION AND EXPLOITATION",
    "KIDNAPPING": "ABDUCTION AND EXPLOITATION"
}

df['Primary Type'] = df['Primary Type'].replace(crime_mapping)

print(df['Primary Type'].unique())

['PROPERTY THEFT' 'OFFENSE INVOLVING CHILDREN' 'HOMICIDE' 'SEX CRIMES'
 'VIOLENT CRIMES' 'OTHER OFFENSE' 'SUBSTANCE CRIMES' 'CRIMINAL TRESPASS'
 'CRIMES AGAINST PUBLIC' 'CONCEALED CARRY LICENSE VIOLATION'
 'ABDUCTION AND EXPLOITATION' 'GAMBLING' 'NON-CRIMINAL']


In [16]:
df['Location Description'] = df['Location Description'].replace({
    "RESIDENCE": "Residential Areas",
    "RESIDENCE - GARAGE": "Residential Areas",
    "APARTMENT": "Residential Areas",
    "RESIDENCE - PORCH / HALLWAY": "Residential Areas",
    "HOUSE": "Residential Areas",
    "YARD": "Residential Areas",
    "RESIDENTIAL YARD (FRONT/BACK)": "Residential Areas",
    "RESIDENCE PORCH/HALLWAY": "Residential Areas",
    "CHA APARTMENT": "Residential Areas",
    "DRIVEWAY - RESIDENTIAL": "Residential Areas",
    "RESIDENCE - YARD (FRONT / BACK)": "Residential Areas",
    "CHA HALLWAY/STAIRWELL/ELEVATOR": "Residential Areas",
    "STREET": "Public Outdoor Spaces",
    "SIDEWALK": "Public Outdoor Spaces",
    "ALLEY": "Public Outdoor Spaces",
    "PARK PROPERTY": "Public Outdoor Spaces",
    "VACANT LOT": "Public Outdoor Spaces",
    "LAKEFRONT/WATERFRONT/RIVERBANK": "Public Outdoor Spaces",
    "FOREST PRESERVE": "Public Outdoor Spaces",
    "BRIDGE": "Public Outdoor Spaces",
    "HIGHWAY / EXPRESSWAY": "Public Outdoor Spaces",
    "PARKING LOT": "Public Outdoor Spaces",
    "GROCERY FOOD STORE": "Commercial and Retail Spaces",
    "SMALL RETAIL STORE": "Commercial and Retail Spaces",
    "DEPARTMENT STORE": "Commercial and Retail Spaces",
    "RETAIL STORE": "Commercial and Retail Spaces",
    "CONVENIENCE STORE": "Commercial and Retail Spaces",
    "BAR OR TAVERN": "Commercial and Retail Spaces",
    "TAVERN / LIQUOR STORE": "Commercial and Retail Spaces",
    "BARBER SHOP/BEAUTY SALON": "Commercial and Retail Spaces",
    "CAR WASH": "Commercial and Retail Spaces",
    "APPLIANCE STORE": "Commercial and Retail Spaces",
    "WAREHOUSE": "Commercial and Retail Spaces",
    "CURRENCY EXCHANGE": "Commercial and Retail Spaces",
    "PAWN SHOP": "Commercial and Retail Spaces",
    "VEHICLE NON-COMMERCIAL": "Transportation-Related Locations",
    "TAXICAB": "Transportation-Related Locations",
    "VEHICLE - COMMERCIAL": "Transportation-Related Locations",
    "VEHICLE - DELIVERY TRUCK": "Transportation-Related Locations",
    "VEHICLE - OTHER RIDE SHARE SERVICE (E.G., UBER, LYFT)": "Transportation-Related Locations",
    "CTA BUS": "Transportation-Related Locations",
    "CTA TRAIN": "Transportation-Related Locations",
    "CTA PLATFORM": "Transportation-Related Locations",
    "AIRPORT TERMINAL LOWER LEVEL - SECURE AREA": "Transportation-Related Locations",
    "AIRPORT BUILDING NON-TERMINAL - NON-SECURE AREA": "Transportation-Related Locations",
    "AIRPORT PARKING LOT": "Transportation-Related Locations",
    "SCHOOL, PUBLIC, BUILDING": "Educational Institutions",
    "SCHOOL, PUBLIC, GROUNDS": "Educational Institutions",
    "SCHOOL, PRIVATE, BUILDING": "Educational Institutions",
    "SCHOOL, PRIVATE, GROUNDS": "Educational Institutions",
    "COLLEGE/UNIVERSITY GROUNDS": "Educational Institutions",
    "COLLEGE/UNIVERSITY RESIDENCE HALL": "Educational Institutions",
    "HOSPITAL BUILDING/GROUNDS": "Healthcare and Emergency Services",
    "MEDICAL/DENTAL OFFICE": "Healthcare and Emergency Services",
    "ANIMAL HOSPITAL": "Healthcare and Emergency Services",
    "NURSING / RETIREMENT HOME": "Healthcare and Emergency Services",
    "JAIL / LOCK-UP FACILITY": "Healthcare and Emergency Services",
    "FIRE STATION": "Healthcare and Emergency Services",
    "SPORTS ARENA/STADIUM": "Recreational and Leisure Areas",
    "BOWLING ALLEY": "Recreational and Leisure Areas",
    "POOL ROOM": "Recreational and Leisure Areas",
    "MOVIE HOUSE/THEATER": "Recreational and Leisure Areas",
    "ATHLETIC CLUB": "Recreational and Leisure Areas",
    "DAY CARE CENTER": "Recreational and Leisure Areas",
    "GOVERNMENT BUILDING/PROPERTY": "Government and Institutional Spaces",
    "FEDERAL BUILDING": "Government and Institutional Spaces",
    "POLICE FACILITY / VEHICLE PARKING LOT": "Government and Institutional Spaces",
    "OTHER": "Miscellaneous",
    "VACANT LOT / LAND": "Miscellaneous",
    "CHA PARKING LOT": "Miscellaneous",
    "CHA GROUNDS": "Miscellaneous"
})

# Check the unique values in the 'Location Description' column after replacement
print(df['Location Description'].unique())


['Residential Areas' 'PARKING LOT / GARAGE (NON RESIDENTIAL)'
 'Public Outdoor Spaces' 'COMMERCIAL / BUSINESS OFFICE' 'OTHER (SPECIFY)'
 'GAS STATION' 'Commercial and Retail Spaces' 'AUTO' 'Miscellaneous'
 'Educational Institutions' 'AUTO / BOAT / RV DEALERSHIP' 'RESTAURANT'
 'RESIDENCE-GARAGE' 'LIBRARY' 'OTHER RAILROAD PROPERTY / TRAIN DEPOT'
 'SCHOOL - PUBLIC GROUNDS' 'HOTEL / MOTEL'
 'Transportation-Related Locations' 'PORCH' 'HOTEL' 'STAIRWELL'
 'CHA PLAY LOT' 'RAILROAD PROPERTY' 'TRAILER' 'GARAGE' 'GANGWAY'
 'CTA SUBWAY STATION' 'BASEMENT' 'CTA "L" PLATFORM'
 'OTHER COMMERCIAL TRANSPORTATION' 'Government and Institutional Spaces'
 'VEHICLE-COMMERCIAL' 'NURSING HOME/RETIREMENT HOME'
 'PARKING LOT/GARAGE(NON.RESID.)' 'Healthcare and Emergency Services'
 'BARBERSHOP' 'POLICE FACILITY/VEH PARKING LOT' 'VACANT LOT/LAND'
 'CTA STATION' 'HOTEL/MOTEL' 'BANK' 'CHA PARKING LOT/GROUNDS'
 'Recreational and Leisure Areas' 'ABANDONED BUILDING'
 'TAVERN/LIQUOR STORE' 'CTA BUS STOP' 'HIGHWAY/EXPR

In [17]:
# Normalize column for consistency
df['Location Description'] = df['Location Description'].str.strip().str.upper()

# Define replacement dictionary
replacement_dict = {
    # Residential Areas
    "RESIDENCE": "Residential Areas",
    "RESIDENCE - GARAGE": "Residential Areas",
    "APARTMENT": "Residential Areas",
    "RESIDENCE-GARAGE": "Residential Areas",
    "HOUSE": "Residential Areas",
    "YARD": "Residential Areas",
    "RESIDENTIAL YARD (FRONT/BACK)": "Residential Areas",
    "RESIDENCE PORCH/HALLWAY": "Residential Areas",
    "CHA APARTMENT": "Residential Areas",
    "DRIVEWAY - RESIDENTIAL": "Residential Areas",
    "RESIDENCE - YARD (FRONT / BACK)": "Residential Areas",

    # Public Outdoor Spaces
    "STREET": "Public Outdoor Spaces",
    "SIDEWALK": "Public Outdoor Spaces",
    "ALLEY": "Public Outdoor Spaces",
    "PARK PROPERTY": "Public Outdoor Spaces",
    "VACANT LOT": "Public Outdoor Spaces",
    "LAKEFRONT/WATERFRONT/RIVERBANK": "Public Outdoor Spaces",
    "FOREST PRESERVE": "Public Outdoor Spaces",
    "BRIDGE": "Public Outdoor Spaces",
    "HIGHWAY / EXPRESSWAY": "Public Outdoor Spaces",
    "PARKING LOT": "Public Outdoor Spaces",

    # Commercial and Retail Spaces
    "GROCERY FOOD STORE": "Commercial and Retail Spaces",
    "SMALL RETAIL STORE": "Commercial and Retail Spaces",
    "DEPARTMENT STORE": "Commercial and Retail Spaces",
    "RETAIL STORE": "Commercial and Retail Spaces",
    "CONVENIENCE STORE": "Commercial and Retail Spaces",
    "BAR OR TAVERN": "Commercial and Retail Spaces",
    "TAVERN / LIQUOR STORE": "Commercial and Retail Spaces",
    "BARBER SHOP/BEAUTY SALON": "Commercial and Retail Spaces",
    "CAR WASH": "Commercial and Retail Spaces",
    "APPLIANCE STORE": "Commercial and Retail Spaces",
    "WAREHOUSE": "Commercial and Retail Spaces",
    "CURRENCY EXCHANGE": "Commercial and Retail Spaces",
    "PAWN SHOP": "Commercial and Retail Spaces",

    # Healthcare and Emergency Services
    "HOSPITAL BUILDING/GROUNDS": "Healthcare and Emergency Services",
    "MEDICAL/DENTAL OFFICE": "Healthcare and Emergency Services",
    "ANIMAL HOSPITAL": "Healthcare and Emergency Services",
    "NURSING / RETIREMENT HOME": "Healthcare and Emergency Services",
    "JAIL / LOCK-UP FACILITY": "Healthcare and Emergency Services",
    "FIRE STATION": "Healthcare and Emergency Services",

    # Transportation-Related Locations
    "VEHICLE NON-COMMERCIAL": "Transportation-Related Locations",
    "TAXICAB": "Transportation-Related Locations",
    "VEHICLE - COMMERCIAL": "Transportation-Related Locations",
    "VEHICLE - DELIVERY TRUCK": "Transportation-Related Locations",
    "VEHICLE - OTHER RIDE SHARE SERVICE (E.G., UBER, LYFT)": "Transportation-Related Locations",
    "CTA BUS": "Transportation-Related Locations",
    "CTA TRAIN": "Transportation-Related Locations",
    "CTA PLATFORM": "Transportation-Related Locations",
    "AIRPORT TERMINAL LOWER LEVEL - SECURE AREA": "Transportation-Related Locations",
    "AIRPORT BUILDING NON-TERMINAL - NON-SECURE AREA": "Transportation-Related Locations",
    "AIRPORT PARKING LOT": "Transportation-Related Locations",

    # Educational Institutions
    "SCHOOL, PUBLIC, BUILDING": "Educational Institutions",
    "SCHOOL, PUBLIC, GROUNDS": "Educational Institutions",
    "SCHOOL, PRIVATE, BUILDING": "Educational Institutions",
    "SCHOOL, PRIVATE, GROUNDS": "Educational Institutions",
    "COLLEGE/UNIVERSITY GROUNDS": "Educational Institutions",
    "COLLEGE/UNIVERSITY RESIDENCE HALL": "Educational Institutions",

    # Recreational and Leisure Areas
    "SPORTS ARENA/STADIUM": "Recreational and Leisure Areas",
    "BOWLING ALLEY": "Recreational and Leisure Areas",
    "POOL ROOM": "Recreational and Leisure Areas",
    "MOVIE HOUSE/THEATER": "Recreational and Leisure Areas",
    "ATHLETIC CLUB": "Recreational and Leisure Areas",
    "DAY CARE CENTER": "Recreational and Leisure Areas",

    # Government and Institutional Spaces
    "GOVERNMENT BUILDING/PROPERTY": "Government and Institutional Spaces",
    "FEDERAL BUILDING": "Government and Institutional Spaces",
    "POLICE FACILITY / VEHICLE PARKING LOT": "Government and Institutional Spaces",

    # Miscellaneous
    "OTHER": "Miscellaneous",
    "VACANT LOT / LAND": "Miscellaneous",
    "CHA PARKING LOT": "Miscellaneous",
    "CHA GROUNDS": "Miscellaneous"
    # Add more mappings as needed
}

# Apply replacements
df['Location Description'] = df['Location Description'].replace(replacement_dict)

# Identify unmatched values
unmatched_values = set(df['Location Description']) - set(replacement_dict.values())
print("Unmatched values:", unmatched_values)


Unmatched values: {'AIRPORT TERMINAL UPPER LEVEL - NON-SECURE AREA', 'CHA PARKING LOT / GROUNDS', 'ABANDONED BUILDING', 'TRANSPORTATION-RELATED LOCATIONS', 'SPORTS ARENA / STADIUM', 'VEHICLE-COMMERCIAL', 'FACTORY/MANUFACTURING BUILDING', 'HOTEL / MOTEL', 'VEHICLE-COMMERCIAL - TROLLEY BUS', 'HEALTHCARE AND EMERGENCY SERVICES', 'SCHOOL - PUBLIC BUILDING', 'AIRPORT TERMINAL MEZZANINE - NON-SECURE AREA', 'OTHER COMMERCIAL TRANSPORTATION', 'MEDICAL / DENTAL OFFICE', 'TAVERN/LIQUOR STORE', 'ATM (AUTOMATIC TELLER MACHINE)', 'GANGWAY', 'FACTORY / MANUFACTURING BUILDING', 'OTHER RAILROAD PROPERTY / TRAIN DEPOT', 'HIGHWAY/EXPRESSWAY', 'PORCH', 'PUBLIC OUTDOOR SPACES', 'BOAT/WATERCRAFT', 'BARBERSHOP', 'LAKEFRONT / WATERFRONT / RIVERBANK', 'CLEANING STORE', 'AIRPORT TERMINAL UPPER LEVEL - SECURE AREA', 'HOSPITAL BUILDING / GROUNDS', 'TRAILER', 'OTHER (SPECIFY)', 'AUTO', 'EDUCATIONAL INSTITUTIONS', 'RAILROAD PROPERTY', 'SCHOOL - PUBLIC GROUNDS', 'CTA BUS STOP', 'MISCELLANEOUS', 'AIRPORT TRANSPORTAT

In [18]:
replacement_dict.update({
    "MEDICAL / DENTAL OFFICE": "Healthcare and Emergency Services",
    "GOVERNMENT BUILDING / PROPERTY": "Government and Institutional Spaces",
    "GAS STATION": "Commercial and Retail Spaces",
    "BOAT/WATERCRAFT": "Transportation-Related Locations",
    "CTA STATION": "Transportation-Related Locations",
    "AIRPORT TRANSPORTATION SYSTEM (ATS)": "Transportation-Related Locations",
    "CTA PARKING LOT / GARAGE / OTHER PROPERTY": "Transportation-Related Locations",
    "COMMERCIAL AND RETAIL SPACES": "Commercial and Retail Spaces",
    "PARKING LOT / GARAGE (NON RESIDENTIAL)": "Public Outdoor Spaces",
    "HIGHWAY/EXPRESSWAY": "Public Outdoor Spaces",
    "GANGWAY": "Residential Areas",
    "ABANDONED BUILDING": "Miscellaneous",
    "COLLEGE / UNIVERSITY - GROUNDS": "Educational Institutions",
    "CTA GARAGE / OTHER PROPERTY": "Transportation-Related Locations",
    "GOVERNMENT AND INSTITUTIONAL SPACES": "Government and Institutional Spaces",
    "HOSPITAL BUILDING / GROUNDS": "Healthcare and Emergency Services",
    "AIRPORT BUILDING NON-TERMINAL - SECURE AREA": "Transportation-Related Locations",
    "CHURCH / SYNAGOGUE / PLACE OF WORSHIP": "Public Outdoor Spaces",
    "AIRPORT TERMINAL UPPER LEVEL - SECURE AREA": "Transportation-Related Locations",
    "HOTEL / MOTEL": "Residential Areas",
    "AIRPORT/AIRCRAFT": "Transportation-Related Locations",
    "VACANT LOT/LAND": "Public Outdoor Spaces",
    "BARBERSHOP": "Commercial and Retail Spaces",
    "POLICE FACILITY/VEH PARKING LOT": "Government and Institutional Spaces",
    "CTA TRACKS - RIGHT OF WAY": "Transportation-Related Locations",
    "CTA SUBWAY STATION": "Transportation-Related Locations",
    "CLEANING STORE": "Commercial and Retail Spaces",
    "COLLEGE / UNIVERSITY - RESIDENCE HALL": "Educational Institutions",
    "SCHOOL - PRIVATE GROUNDS": "Educational Institutions",
    "VEHICLE - OTHER RIDE SHARE SERVICE (LYFT, UBER, ETC.)": "Transportation-Related Locations",
    "CTA 'L' PLATFORM": "Transportation-Related Locations",
    "AIRPORT EXTERIOR - NON-SECURE AREA": "Transportation-Related Locations",
    "AIRCRAFT": "Transportation-Related Locations",
    "AUTO": "Transportation-Related Locations",
    "KENNEL": "Miscellaneous",
    "AIRPORT TERMINAL UPPER LEVEL - NON-SECURE AREA": "Transportation-Related Locations",
    "FARM": "Miscellaneous",
    "SAVINGS AND LOAN": "Commercial and Retail Spaces",
    "LAKEFRONT / WATERFRONT / RIVERBANK": "Public Outdoor Spaces",
    "BOAT / WATERCRAFT": "Transportation-Related Locations",
    "PORCH": "Residential Areas",
    "CONSTRUCTION SITE": "Miscellaneous",
    "AUTO / BOAT / RV DEALERSHIP": "Commercial and Retail Spaces",
    "LIBRARY": "Public Outdoor Spaces",
    "VEHICLE-COMMERCIAL": "Transportation-Related Locations",
    "CHA PARKING LOT / GROUNDS": "Transportation-Related Locations",
    "COIN OPERATED MACHINE": "Commercial and Retail Spaces",
    "RAILROAD PROPERTY": "Transportation-Related Locations",
    "COMMERCIAL / BUSINESS OFFICE": "Commercial and Retail Spaces",
    "NEWSSTAND": "Commercial and Retail Spaces",
    "OTHER (SPECIFY)": "Miscellaneous",
    "STAIRWELL": "Residential Areas",
    "SCHOOL - PRIVATE BUILDING": "Educational Institutions",
    "ATM (AUTOMATIC TELLER MACHINE)": "Commercial and Retail Spaces",
    "TRANSPORTATION-RELATED LOCATIONS": "Transportation-Related Locations",
    "OTHER COMMERCIAL TRANSPORTATION": "Transportation-Related Locations",
    "VEHICLE-COMMERCIAL - TROLLEY BUS": "Transportation-Related Locations",
    "CHA PARKING LOT/GROUNDS": "Transportation-Related Locations",
    "AIRPORT TERMINAL MEZZANINE - NON-SECURE AREA": "Transportation-Related Locations",
    "RECREATIONAL AND LEISURE AREAS": "Recreational and Leisure Areas",
    "FACTORY / MANUFACTURING BUILDING": "Miscellaneous",
    "GARAGE": "Residential Areas",
    "BASEMENT": "Residential Areas",
    "HOTEL/MOTEL": "Residential Areas",
    "RESIDENTIAL AREAS": "Residential Areas",
    "TAVERN/LIQUOR STORE": "Commercial and Retail Spaces",
    "HORSE STABLE": "Miscellaneous",
    "CTA BUS STOP": "Transportation-Related Locations",
    "RESTAURANT": "Commercial and Retail Spaces",
    "TRAILER": "Miscellaneous",
    "SCHOOL - PUBLIC BUILDING": "Educational Institutions",
    "BANK": "Commercial and Retail Spaces",
    "CHURCH/SYNAGOGUE/PLACE OF WORSHIP": "Public Outdoor Spaces",
    "AIRPORT EXTERIOR - SECURE AREA": "Transportation-Related Locations",
    "SCHOOL - PUBLIC GROUNDS": "Educational Institutions",
    "SPORTS ARENA / STADIUM": "Recreational and Leisure Areas",
    "OTHER RAILROAD PROPERTY / TRAIN DEPOT": "Transportation-Related Locations",
    "PUBLIC OUTDOOR SPACES": "Public Outdoor Spaces",
    "AIRPORT VENDING ESTABLISHMENT": "Transportation-Related Locations",
    "PARKING LOT/GARAGE(NON.RESID.)": "Public Outdoor Spaces",
    "HOTEL": "Residential Areas",
    "OTHER RAILROAD PROP / TRAIN DEPOT": "Transportation-Related Locations",
    "CEMETARY": "Miscellaneous",
    "CHA PLAY LOT": "Public Outdoor Spaces",
    "HEALTHCARE AND EMERGENCY SERVICES": "Healthcare and Emergency Services",
    "VEHICLE-COMMERCIAL - ENTERTAINMENT/PARTY BUS": "Transportation-Related Locations",
    "CREDIT UNION": "Commercial and Retail Spaces",
    "NURSING HOME/RETIREMENT HOME": "Healthcare and Emergency Services",
    "FACTORY/MANUFACTURING BUILDING": "Miscellaneous",
    "AIRPORT TERMINAL LOWER LEVEL - NON-SECURE AREA": "Transportation-Related Locations",
    "DRUG STORE": "Commercial and Retail Spaces"
})
# Apply updated replacements
df['Location Description'] = df['Location Description'].replace(replacement_dict)

# Identify any remaining unmatched values
unmatched_values = set(df['Location Description']) - set(replacement_dict.values())
print("Unmatched values:", unmatched_values)


Unmatched values: {'EDUCATIONAL INSTITUTIONS', 'CTA "L" PLATFORM', 'MISCELLANEOUS'}


In [19]:
# Update replacement dictionary for remaining unmatched values
replacement_dict.update({
    "CTA \"L\" PLATFORM": "Transportation-Related Locations",
    "EDUCATIONAL INSTITUTIONS": "Educational Institutions",
    "MISCELLANEOUS": "Miscellaneous",

})

# Apply updated replacements
df['Location Description'] = df['Location Description'].replace(replacement_dict)

# Check again for unmatched values
unmatched_values = set(df['Location Description']) - set(replacement_dict.values())
print("Unmatched values:", unmatched_values)


Unmatched values: set()


In [20]:
# One-hot encode 'Primary Type'
primary_type_dummies = pd.get_dummies(df['Primary Type'], prefix='Primary_Type', dtype=int)
df = pd.concat([df, primary_type_dummies], axis=1)

# One-hot encode 'Location Description'
location_description_dummies = pd.get_dummies(df['Location Description'], prefix='Location_Description', dtype=int)
df = pd.concat([df, location_description_dummies], axis=1)

# Display the updated DataFrame (optional)
df.head()

ID                Date                Block  \
0  11662417 2019-04-21 12:30:00      009XX E 80TH ST   
1  12990873 2019-08-17 13:14:00   008XX N KARLOV AVE   
4  11765926 2019-07-21 14:00:00      002XX W 87TH ST   
5  11885224 2019-11-05 20:00:00   075XX S RHODES AVE   
9  11842146 2019-09-26 20:53:00  083XX S SANGAMON ST   

                 Primary Type   Location Description  Arrest  Domestic  Beat  \
0              PROPERTY THEFT      Residential Areas   False     False   631   
1  OFFENSE INVOLVING CHILDREN      Residential Areas    True      True  1111   
4              PROPERTY THEFT  Public Outdoor Spaces   False     False   622   
5              PROPERTY THEFT  Public Outdoor Spaces   False      True   624   
9              PROPERTY THEFT      Residential Areas   False      True   613   

   District  Ward  ...  Primary_Type_VIOLENT CRIMES  \
0         6   8.0  ...                            0   
1        11  37.0  ...                            0   
4         6  21.0  ...                            0   
5         6   6.0  ...                            0   
9         6  17.0  ...                            0   

   Location_Description_Commercial and Retail Spaces  \
0                                                  0   
1                                                  0   
4                                                  0   
5                                                  0   
9                                                  0   

   Location_Description_Educational Institutions  \
0                                              0   
1                                              0   
4                                              0   
5                                              0   
9                                              0   

   Location_Description_Government and Institutional Spaces  \
0                                                  0          
1                                                  0          
4                                                  0          
5                                                  0          
9                                                  0          

   Location_Description_Healthcare and Emergency Services  \
0                                                  0        
1                                                  0        
4                                                  0        
5                                                  0        
9                                                  0        

  Location_Description_Miscellaneous  \
0                                  0   
1                                  0   
4                                  0   
5                                  0   
9                                  0   

   Location_Description_Public Outdoor Spaces  \
0                                           0   
1                                           0   
4                                           1   
5                                           1   
9                                           0   

   Location_Description_Recreational and Leisure Areas  \
0                                                  0     
1                                                  0     
4                                                  0     
5                                                  0     
9                                                  0     

   Location_Description_Residential Areas  \
0                                       1   
1                                       1   
4                                       0   
5                                       0   
9                                       1   

   Location_Description_Transportation-Related Locations  
0                                                  0      
1                                                  0      
4                                                  0      
5                                                  0      
9            

In [21]:
df_for_modeling = df.drop(columns=['ID','Date','Block','Primary Type','Location Description','Beat','District','Ward','Community Area'])

In [22]:
Y = ['Longitude', 'Latitude', 'Location', 'X Coordinate', 'Y Coordinate']
X = df_for_modeling.drop(columns=Y)
print(X.columns)

Index(['Arrest', 'Domestic', 'hour', 'day_of_week', 'month', 'year',
       'hour_sin', 'hour_cos', 'day_of_week_sin', 'day_of_week_cos',
       'mont_sin', 'month_cos', 'Primary_Type_ABDUCTION AND EXPLOITATION',
       'Primary_Type_CONCEALED CARRY LICENSE VIOLATION',
       'Primary_Type_CRIMES AGAINST PUBLIC', 'Primary_Type_CRIMINAL TRESPASS',
       'Primary_Type_GAMBLING', 'Primary_Type_HOMICIDE',
       'Primary_Type_NON-CRIMINAL', 'Primary_Type_OFFENSE INVOLVING CHILDREN',
       'Primary_Type_OTHER OFFENSE', 'Primary_Type_PROPERTY THEFT',
       'Primary_Type_SEX CRIMES', 'Primary_Type_SUBSTANCE CRIMES',
       'Primary_Type_VIOLENT CRIMES',
       'Location_Description_Commercial and Retail Spaces',
       'Location_Description_Educational Institutions',
       'Location_Description_Government and Institutional Spaces',
       'Location_Description_Healthcare and Emergency Services',
       'Location_Description_Miscellaneous',
       'Location_Description_Public Outdoor Space

In [23]:
from sklearn.model_selection import train_test_split

In [24]:
X_train, X_test, y_train, y_test = train_test_split(X, df_for_modeling[Y], test_size=0.2, random_state=42)

In [25]:
from sklearn.preprocessing import StandardScaler

In [26]:
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X)
X_test_scaled = scaler.transform(X)

In [27]:
Y = df_for_modeling[['Longitude', 'Latitude', 'Location', 'X Coordinate', 'Y Coordinate']]

In [28]:
from scipy.stats import gaussian_kde

def spatial_kernel(x, y, hx, hy):
    return np.exp(-(x ** 2 / hx ** 2 + y ** 2 / hy ** 2) / 2)

def temporal_kernel(t, ht):
    return np.exp(-(t ** 2 / ht ** 2) / 2)


In [29]:
def stkde(data, grid, hx, hy, ht):
    """
    Spatio-Temporal Kernel Density Estimation.

    Parameters:
    - data: DataFrame with columns ['Longitude', 'Latitude', 'Time']
    - grid: Grid coordinates [(x, y, t)]
    - hx, hy, ht: Bandwidths for spatial and temporal dimensions

    Returns:
    - density_estimates: STKDE values for each grid cell
    """
    density_estimates = []
    for (gx, gy, gt) in grid:
        density = 0
        for _, row in data.iterrows():
            spatial = spatial_kernel(gx - row['Longitude'], gy - row['Latitude'], hx, hy)
            temporal = temporal_kernel(gt - row['Time'], ht)
            density += spatial * temporal
        density_estimates.append(density)
    return np.array(density_estimates)


In [30]:
def create_grid(data, x_step, y_step, t_step):
    x_min, x_max = data['Longitude'].min(), data['Longitude'].max()
    y_min, y_max = data['Latitude'].min(), data['Latitude'].max()
    t_min, t_max = data['Time'].min(), data['Time'].max()

    x_coords = np.arange(x_min, x_max, x_step)
    y_coords = np.arange(y_min, y_max, y_step)
    t_coords = np.arange(t_min, t_max, t_step)

    return [(x, y, t) for x in x_coords for y in y_coords for t in t_coords]


In [31]:
# Check required columns exist
required_columns = {'Latitude', 'Longitude', 'hour', 'day_of_week', 'month', 'year'}
assert required_columns.issubset(df_for_modeling.columns), f"Missing required columns: {required_columns - set(df_for_modeling.columns)}"

# Create a unified temporal feature
# Scale and normalize the temporal components for comparability
df_for_modeling['Time'] = (
    df_for_modeling['year'] * 365 * 24 + df_for_modeling['month'] * 30 * 24 + df_for_modeling['day_of_week'] * 24 + df_for_modeling['hour']
)


In [33]:
def spatial_kernel(x, y, hx, hy):
    return np.exp(-(x ** 2 / hx ** 2 + y ** 2 / hy ** 2) / 2)

def temporal_kernel(t, ht):
    return np.exp(-(t ** 2 / ht ** 2) / 2)


In [34]:
def create_grid(data, x_step, y_step, t_step):
    x_min, x_max = data['Longitude'].min(), data['Longitude'].max()
    y_min, y_max = data['Latitude'].min(), data['Latitude'].max()
    t_min, t_max = data['Time'].min(), data['Time'].max()

    x_coords = np.arange(x_min, x_max, x_step)
    y_coords = np.arange(y_min, y_max, y_step)
    t_coords = np.arange(t_min, t_max, t_step)

    return [(x, y, t) for x in x_coords for y in y_coords for t in t_coords]


In [35]:
def stkde(data, grid, hx, hy, ht):
    density_estimates = []
    for (gx, gy, gt) in grid:
        density = 0
        for _, row in data.iterrows():
            spatial = spatial_kernel(gx - row['Longitude'], gy - row['Latitude'], hx, hy)
            temporal = temporal_kernel(gt - row['Time'], ht)
            density += spatial * temporal
        density_estimates.append(density)
    return np.array(density_estimates)


In [36]:
def visualize_density(grid, density):
    grid = np.array(grid)
    x_coords, y_coords = grid[:, 0], grid[:, 1]

    # Reshape density for plotting
    density_reshaped = density.reshape(len(np.unique(x_coords)), len(np.unique(y_coords)))

    # Plot as heatmap
    plt.figure(figsize=(10, 8))
    plt.imshow(density_reshaped.T, origin='lower', cmap='hot', extent=(x_coords.min(), x_coords.max(), y_coords.min(), y_coords.max()))
    plt.colorbar(label='Density')
    plt.xlabel('Longitude')
    plt.ylabel('Latitude')
    plt.title('Spatio-Temporal Kernel Density Estimation')
    plt.show()


In [ ]:
# Check required columns exist
required_columns = {'Latitude', 'Longitude', 'hour', 'day_of_week', 'month', 'year'}
assert required_columns.issubset(df_for_modeling.columns), f"Missing required columns: {required_columns - set(df_for_modeling.columns)}"

# Create a unified temporal feature
# Scale and normalize the temporal components for comparability
df_for_modeling['Time'] = (
    df_for_modeling['year'] * 365 * 24 + df_for_modeling['month'] * 30 * 24 + df_for_modeling['day_of_week'] * 24 + df_for_modeling['hour']
)

# Update the stkde function to use the new 'Time' column
def stkde(data, grid, hx, hy, ht):
    density_estimates = []
    for (gx, gy, gt) in grid:
        density = 0
        for _, row in data.iterrows():
            spatial = spatial_kernel(gx - row['Longitude'], gy - row['Latitude'], hx, hy)
            temporal = temporal_kernel(gt - row['Time'], ht) # Use 'Time' column
            density += spatial * temporal
        density_estimates.append(density)
    return np.array(density_estimates)

# Define bandwidth parameters (you might need to adjust these)
hx = 0.01
hy = 0.01
ht = 1000

# Create the grid
grid = create_grid(df_for_modeling, x_step=0.01, y_step=0.01, t_step=1000) # Define step sizes


# And in the main code:
#Run STKDE
density = stkde(df_for_modeling, grid, hx, hy, ht) # Use 'df_for_modeling' instead of 'df'